# CatBoost

2017 Yandex rusların ilk açık kaynak kodlu ml dosyası

Normal değişknelerde (özellikler sürekli değişknelerde) çokta yüksek  performansı değil 

ancak ketegoric değişkenkş data setlerde başarısını gösteririr
    
Zaten özelliği de bu cetegorik değişkneleri otomatik olarak mücadele edebiliyor

In [2]:
import numpy as np
import pandas as pd 
from sklearn.model_selection import train_test_split, GridSearchCV,cross_val_score
from sklearn.metrics import mean_squared_error, r2_score
import matplotlib.pyplot as plt
from sklearn.preprocessing import scale 
from sklearn import model_selection
from sklearn.tree import DecisionTreeRegressor, DecisionTreeClassifier
from sklearn.neighbors import KNeighborsRegressor
from sklearn.ensemble import BaggingRegressor

from warnings import filterwarnings
filterwarnings('ignore')

In [3]:
hit = pd.read_csv("Hitters.csv")
df = hit.copy()
df = df.dropna()
dms = pd.get_dummies(df[['League', 'Division', 'NewLeague']])
y = df["Salary"]
X_ = df.drop(['Salary', 'League', 'Division', 'NewLeague'], axis=1).astype('float64')
X = pd.concat([X_, dms[['League_N', 'Division_W', 'NewLeague_N']]], axis=1)
X_train, X_test, y_train, y_test = train_test_split(X, y, 
                                                    test_size=0.25, 
                                                    random_state=42)

In [4]:
from catboost import CatBoostRegressor

In [5]:
param_grid={"iterations":[150,200],
        "learning_rate":[0.01,0.02,0.03,0.05,0.1],
        "depth":[6,7,8]}
        

In [6]:
cat=CatBoostRegressor()

In [7]:
cat_cv=GridSearchCV(estimator=cat,param_grid=param_grid,cv=2,n_jobs=-1)
cat_cv.fit(X_train,y_train)

0:	learn: 383.9742072	total: 58.5ms	remaining: 8.72s
1:	learn: 381.9044902	total: 60.2ms	remaining: 4.46s
2:	learn: 380.1504985	total: 61.5ms	remaining: 3.01s
3:	learn: 378.1661143	total: 65.3ms	remaining: 2.38s
4:	learn: 376.3050509	total: 67.2ms	remaining: 1.95s
5:	learn: 374.6412451	total: 70.8ms	remaining: 1.7s
6:	learn: 373.2676164	total: 72ms	remaining: 1.47s
7:	learn: 371.7086654	total: 73ms	remaining: 1.29s
8:	learn: 370.0131359	total: 74.1ms	remaining: 1.16s
9:	learn: 368.3649663	total: 75.2ms	remaining: 1.05s
10:	learn: 366.8445421	total: 76.2ms	remaining: 963ms
11:	learn: 365.2407506	total: 77.6ms	remaining: 892ms
12:	learn: 363.4927580	total: 78.7ms	remaining: 829ms
13:	learn: 361.7657174	total: 79.7ms	remaining: 774ms
14:	learn: 360.4227164	total: 80.8ms	remaining: 727ms
15:	learn: 358.8113683	total: 82.4ms	remaining: 690ms
16:	learn: 357.4166475	total: 84ms	remaining: 657ms
17:	learn: 355.9286185	total: 86.7ms	remaining: 636ms
18:	learn: 354.2663935	total: 88.1ms	remainin

GridSearchCV(cv=2,
             estimator=<catboost.core.CatBoostRegressor object at 0x157a78460>,
             n_jobs=-1,
             param_grid={'depth': [6, 7, 8], 'iterations': [150, 200],
                         'learning_rate': [0.01, 0.02, 0.03, 0.05, 0.1]})

In [10]:
from catboost import CatBoost


model = CatBoost()

grid = {'learning_rate': [0.03, 0.1],
        'depth': [4, 6, 10],
        'l2_leaf_reg': [1, 3, 5, 7, 9]} #hocam buradaki sayıları arttırdıkça model kurulumu yavaşalr daha da artırırssan hata verir kurmaaz :))

grid_search_result = model.grid_search(grid, 
                                       X=X_train, 
                                       y=y_train, 
                                       plot=True)


MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 692.4709195	test: 659.2358580	best: 659.2358580 (0)	total: 1.52ms	remaining: 1.52s
1:	learn: 677.0753778	test: 644.7508324	best: 644.7508324 (1)	total: 2.8ms	remaining: 1.4s
2:	learn: 662.7316316	test: 631.5846491	best: 631.5846491 (2)	total: 3.78ms	remaining: 1.25s
3:	learn: 649.9749804	test: 620.0066704	best: 620.0066704 (3)	total: 5.14ms	remaining: 1.28s
4:	learn: 637.6347802	test: 607.3946875	best: 607.3946875 (4)	total: 7.03ms	remaining: 1.4s
5:	learn: 624.2989785	test: 594.6476876	best: 594.6476876 (5)	total: 7.97ms	remaining: 1.32s
6:	learn: 611.3339336	test: 583.9188649	best: 583.9188649 (6)	total: 8.32ms	remaining: 1.18s
7:	learn: 598.4670609	test: 571.2889831	best: 571.2889831 (7)	total: 9.73ms	remaining: 1.21s
8:	learn: 586.4228108	test: 559.8610738	best: 559.8610738 (8)	total: 10.5ms	remaining: 1.15s
9:	learn: 574.4119753	test: 547.8901630	best: 547.8901630 (9)	total: 11.7ms	remaining: 1.16s
10:	learn: 561.8540153	test: 536.5830646	best: 536.5830646 (10)	total: 12

In [8]:
cat_cv.best_params_

{'depth': 7, 'iterations': 200, 'learning_rate': 0.05}

In [9]:
cat_final=CatBoostRegressor(depth=7,iterations=200,learning_rate=0.05).fit(X_train,y_train)
np.sqrt(mean_squared_error(y_test,cat_final.predict(X_test)))

0:	learn: 433.3834544	total: 3.29ms	remaining: 654ms
1:	learn: 424.4856008	total: 6.6ms	remaining: 653ms
2:	learn: 414.9854065	total: 8.24ms	remaining: 541ms
3:	learn: 406.2185525	total: 9.39ms	remaining: 460ms
4:	learn: 399.2402687	total: 10.4ms	remaining: 406ms
5:	learn: 390.1812179	total: 11.3ms	remaining: 366ms
6:	learn: 380.4704802	total: 12.4ms	remaining: 342ms
7:	learn: 371.0329213	total: 13.3ms	remaining: 319ms
8:	learn: 363.8087914	total: 14.8ms	remaining: 315ms
9:	learn: 357.6713364	total: 16ms	remaining: 304ms
10:	learn: 350.9641495	total: 18.7ms	remaining: 322ms
11:	learn: 344.0856301	total: 21.2ms	remaining: 332ms
12:	learn: 337.4508426	total: 23.2ms	remaining: 333ms
13:	learn: 330.6494265	total: 24.4ms	remaining: 324ms
14:	learn: 324.4279713	total: 26ms	remaining: 321ms
15:	learn: 318.2569582	total: 27ms	remaining: 311ms
16:	learn: 312.2819478	total: 28ms	remaining: 301ms
17:	learn: 306.4212227	total: 28.9ms	remaining: 292ms
18:	learn: 300.9507106	total: 29.9ms	remaining:

351.6451068858999